In [3]:
from scipy.sparse import csc_matrix
import trimesh
import skeletor as sk
from util.mesh import MeshProcessor
#mesh = trimesh.load("/Users/ackermand/Documents/Downloads/410_roi1.obj")
id=45
mp = MeshProcessor(path = "https://janelia-cosem-datasets.s3.amazonaws.com/jrc_mus-liver/neuroglancer/mesh/mito_seg",lod = 2, min_branch_length = 20)
mesh = mp.get_mesh(id=id)
#trimesh_mesh = trimesh.Trimesh(ms.current_mesh().vertex_matrix(), ms.current_mesh().face_matrix())
_ = mesh.export(f"{id}.ply")



In [ ]:
trimesh_mesh.show()

In [4]:
#mesh = sk.pre.fix_mesh(mesh, remove_disconnected=5, inplace=False)
mesh_contracted = sk.pre.contract(mesh,iter_lim=30, epsilon=0.5)#,iter_lim=15)# epsilon=0.1,SL=5)


  2%|▏         | [00:03<02:33, 13/30it,  1.57s/it, epsilon 0.99

Total face area increased from last iteration. Contraction stopped prematurely after 12 iterations at epsilon 0.99.


In [5]:
#skel = sk.skeletonize.by_tangent_ball(mesh)# 
#skel = sk.skeletonize.by_wavefront(mesh, waves=1, step_size=1)
#skel = sk.skeletonize.by_teasar(mesh_contracted, inv_dist = 10)
skel = sk.skeletonize.by_vertex_clusters(mesh_contracted,sampling_dist=10)
skel = sk.post.clean_up(skel)


Clustering: 100%|██████████| 10592/10592 [00:00<00:00, 69300.30it/s]


In [1]:
import navis
import numpy as np
from navis import graph
n = navis.TreeNeuron(skel, soma=None)
pruned = navis.prune_twigs(n,100,recursive=True)
seg_lengths_before = np.array([graph.segment_length(n, s) for s in n.segments])
seg_lengths_after = np.array([graph.segment_length(pruned, s) for s in pruned.segments])

print(seg_lengths_before,seg_lengths_after)
skel2 = sk.Skeleton(pruned.nodes[['node_id', 'parent_id', 'x', 'y', 'z', 'radius']],mesh=mesh)
print(n.n_leafs,pruned.n_leafs)
skel2 = sk.post.clean_up(skel2)
n2 = navis.TreeNeuron(skel2, soma=None)
longest_path = navis.longest_neurite(n2, from_root=False)
navis.plot3d([n2,longest_path, mesh])

/Users/ackermand/miniconda3/envs/mesh_playground/lib/python3.7/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


NameError: name 'skel' is not defined

In [43]:
print(len(mesh.vertices))

9605


In [ ]:
import numpy as np
import time
metric = np.random.random(len(mesh.vertices))
t = time.time()
face_metrics = np.mean(metric[mesh.faces.flatten()].reshape((-1,3)),axis=1)


In [ ]:

import numpy as np
import time
e = np.array(mesh.edges)
t = time.time()
temp = csc_matrix((np.ones(len(e)),(e[:,0],e[:,1])), shape=(len(mesh.vertices),len(mesh.vertices)))
print(time.time()-t)
t = time.time()
for i in range(10):
    temp = temp.dot(temp)
print(type(temp))
print(time.time()-t)
rows,cols = temp.nonzero()
cols[rows==0]

In [ ]:
g = nx.from_edgelist(mesh.edges_unique)

In [ ]:
a = dict(nx.all_pairs_shortest_path_length(g,cutoff=5))

In [ ]:
a[0][0]

In [6]:
import pyglet
window = pyglet.window.Window()
label = pyglet.text.Label('Hello, world',
                          font_name='Times New Roman',
                          font_size=36,
                          x=window.width//2, y=window.height//2,
                          anchor_x='center', anchor_y='center')

@window.event
def on_draw():
    window.clear()
    label.draw()

pyglet.app.run()

2022-09-13 23:00:42.985 python[7829:106557] Warning: Expected min height of view: (<NSPopoverTouchBarItemButton: 0x7ff3cc979ec0>) to be less than or equal to 30 but got a height of 32.000000. This error will be logged once per view in violation.
2022-09-13 23:00:42.986 python[7829:106557] Warning: Expected min height of view: (<NSButton: 0x7ff3ccb928f0>) to be less than or equal to 30 but got a height of 32.000000. This error will be logged once per view in violation.
2022-09-13 23:00:42.989 python[7829:106557] Warning: Expected min height of view: (<NSPopoverTouchBarItemButton: 0x7ff3cb7faa80>) to be less than or equal to 30 but got a height of 32.000000. This error will be logged once per view in violation.
2022-09-13 23:00:42.991 python[7829:106557] Warning: Expected min height of view: (<NSPopoverTouchBarItemButton: 0x7ff3ccd7d550>) to be less than or equal to 30 but got a height of 32.000000. This error will be logged once per view in violation.


: 

In [ ]:
import numpy as np
a = np.arange(10)
a.clip(4,7)
print(a)

In [ ]:
import pymeshlab
import numpy as np
ms = pymeshlab.MeshSet()
ms.load_new_mesh("/Users/ackermand/Documents/Downloads/410_roi1.obj")
# ms.load_new_mesh("./content/MPI-FAUST/meshes/tr_reg_000.ply")
mesh = ms.current_mesh()
t = time.time()
ms.meshing_repair_non_manifold_edges()
t=time.time()
ms.compute_scalar_by_geodesic_distance_from_given_point_per_vertex(np.array[mesh.vertex_matrix()[0,:]])
print(time.time()-t)

In [ ]:
print(mesh.vertex_matrix()[0,:])
t=time.time()
ms.compute_scalar_by_geodesic_distance_from_given_point_per_vertex(startpoint = mesh.vertex_matrix()[0,:],maxdistance=pymeshlab.Percentage(1))
print(time.time()-t)

In [7]:
from util.mesh import MeshProcessor
from tqdm import tqdm
import numpy as np

mp = MeshProcessor(path = "https://janelia-cosem-datasets.s3.amazonaws.com/jrc_hela-2/neuroglancer/mesh/mito_seg",lod = 0, min_branch_length = 20, )
#mp.process_mesh(id=53994)
#mp.process_mesh(id=84602)
#mp.process_mesh(id=322)
#mp.process_mesh(id=116)
momenta = np.zeros((421,3),dtype=np.float32)
for i in tqdm(range(1,422)):
    momenta[i-1,:] = mp.process_mesh(id=i)




  0%|          | 0/421 [00:00<?, ?it/s]


ValueError: setting an array element with a sequence.

In [2]:
from util.mesh import MeshProcessor
from tqdm import tqdm
import numpy as np
import dask
from dask.distributed import Client, progress
import pandas as pd

client = Client(threads_per_worker=2, n_workers=1)
client.cluster.scale(8)
print(client.dashboard_link)
mp = MeshProcessor(path = "https://janelia-cosem-datasets.s3.amazonaws.com/jrc_hela-2/neuroglancer/mesh/mito_seg",lod = 2, min_branch_length = 100, use_skeletons=True)
#momenta = np.zeros((421,3),dtype=np.float32)
lazy_results = []
for i in range(1,422,1):#range(1,87077,100): #
    lazy_results.append(mp.process_mesh(id=i))
results = dask.compute(*lazy_results)
df = pd.DataFrame.from_records(results)
temp = df[["principal_inertia_component_0","principal_inertia_component_1","principal_inertia_component_2"]].to_numpy()>=0
print(temp.all())


http://127.0.0.1:8787/status


distributed.diskutils - INFO - Found stale lock file and directory '/Users/ackermand/Programming/mesh_playground/dask-worker-space/worker-wbeohlcp', purging
distributed.diskutils - INFO - Found stale lock file and directory '/Users/ackermand/Programming/mesh_playground/dask-worker-space/worker-atdz66ws', purging
distributed.diskutils - INFO - Found stale lock file and directory '/Users/ackermand/Programming/mesh_playground/dask-worker-space/worker-vsnvbev7', purging
distributed.diskutils - INFO - Found stale lock file and directory '/Users/ackermand/Programming/mesh_playground/dask-worker-space/worker-00oc6nh4', purging
distributed.diskutils - INFO - Found stale lock file and directory '/Users/ackermand/Programming/mesh_playground/dask-worker-space/worker-9wydzwv0', purging
distributed.diskutils - INFO - Found stale lock file and directory '/Users/ackermand/Programming/mesh_playground/dask-worker-space/worker-gf6ad35h', purging
distributed.diskutils - INFO - Found stale lock file and d

True


In [2]:
temp = df[["principal_inertia_component_0","principal_inertia_component_1","principal_inertia_component_2"]].to_numpy()>=0
temp.all()

True

In [3]:
print(df.to_string())

      id        volume  surface_area  principal_inertia_component_0  principal_inertia_component_normalized_0  principal_inertia_component_1  principal_inertia_component_normalized_1  principal_inertia_component_2  principal_inertia_component_normalized_2  num_fragments  num_branches  longest_path
0      1  6.089691e+06  2.403698e+05                   1.401700e+10                                  0.045627                   1.448537e+11                                  0.471512                   1.483402e+11                                  0.482861              1             0    579.152499
1      2  5.372239e+05  3.709387e+04                   4.831928e+08                                  0.256861                   5.866144e+08                                  0.311839                   8.113388e+08                                  0.431300              1             0    128.265584
2      3  3.795491e+06  1.730737e+05                   1.564522e+10                                  0.

In [55]:
from util.mesh import MeshProcessor
mp = MeshProcessor(path = "https://janelia-cosem-datasets.s3.amazonaws.com/jrc_hela-2/neuroglancer/mesh/mito_seg",lod = 2, min_branch_length = 100, use_skeletons=True,close_holes=True)
mesh = mp.get_mesh(276)
#mp.process_mesh(id=325).compute()

In [58]:
mesh.show()

In [5]:
import trimesh
import numpy as np
#mesh = trimesh.load_mesh("41401.ply")
#print(mesh.is_watertight)
#print(mesh.volume, mesh.area, mesh.principal_inertia_components)
#mesh.apply_transform(mesh.principal_inertia_transform)
scene = trimesh.Scene()
for index, row in df.iterrows():
    if index<10:
        scene.add_geometry(row['mesh'])

#scene.add_geometry(mesh)
#axis = trimesh.creation.axis(origin_color=[1., 0, 0])
#scene.add_geometry(axis)
scene.show()


In [2]:
temp = df[["principal_inertia_component_0","principal_inertia_component_1","principal_inertia_component_2"]].to_numpy()>=0
temp.all()


False

In [ ]:
from sklearn.decomposition import PCA
row_norms = np.sum(momenta,axis=1)
normalized_momenta = momenta/row_norms[:,np.newaxis]
pca = PCA(n_components=3)
pca.fit(normalized_momenta)
transformed = pca.transform(normalized_momenta)

In [ ]:
import matplotlib.pyplot as plt
fig = plt.figure()
ax = fig.add_subplot()#projection='3d')
ax.scatter(normalized_momenta[:,2],normalized_momenta[:,0])
print(normalized_momenta[280,:],normalized_momenta[44,:],normalized_momenta[200,:])

In [4]:
from sklearn.cluster import KMeans,SpectralClustering
from sklearn.preprocessing import StandardScaler
data = df[["longest_path","num_fragments","volume","principal_inertia_component_normalized_0","principal_inertia_component_normalized_1","principal_inertia_component_normalized_2"]].to_numpy()
#data = df[["longest_path","num_fragments"]].to_numpy()

data = StandardScaler().fit(data).transform(data)
n_clusters = 5
#clustering = KMeans(n_clusters=5, random_state=0).fit(data)
clustering = SpectralClustering(n_clusters=n_clusters,
             assign_labels='discretize',
             random_state=0).fit(data)
for label in range(n_clusters):
    print([int(df.iloc[i]["id"]) for i, x in enumerate(clustering.labels_==label) if x])

[1, 4, 7, 11, 22, 26, 28, 32, 34, 35, 41, 42, 45, 55, 59, 60, 61, 64, 65, 74, 76, 78, 80, 83, 85, 87, 89, 92, 94, 95, 96, 99, 108, 109, 113, 114, 116, 118, 122, 129, 138, 139, 143, 146, 147, 148, 150, 151, 152, 156, 159, 161, 162, 166, 168, 173, 176, 182, 184, 186, 190, 192, 197, 199, 200, 201, 205, 206, 210, 211, 213, 216, 218, 229, 240, 244, 251, 255, 258, 260, 263, 271, 272, 273, 276, 278, 285, 288, 290, 292, 294, 297, 303, 309, 310, 311, 312, 319, 322, 325, 328, 329, 330, 336, 337, 340, 343, 344, 347, 351, 352, 353, 356, 359, 361, 363, 365, 366, 373, 374, 385, 388, 390, 392, 401, 406, 413, 416, 420, 421]
[5, 10, 16, 20, 27, 33, 36, 37, 38, 40, 43, 44, 47, 48, 49, 53, 56, 58, 68, 69, 72, 81, 82, 88, 90, 97, 98, 104, 107, 110, 112, 115, 117, 119, 120, 124, 130, 132, 133, 137, 145, 149, 157, 158, 160, 169, 170, 172, 179, 180, 189, 191, 203, 207, 208, 209, 214, 215, 221, 222, 226, 228, 230, 233, 235, 236, 237, 242, 247, 249, 250, 253, 256, 259, 266, 268, 270, 280, 281, 284, 289, 291, 2

In [19]:
int(df.iloc[0]["id"])

1

In [12]:
import colorsys
def highlight_color(rgb):
    r = rgb[0]/255.0
    g = rgb[1]/255.0
    b = rgb[2]/255.0
    print((r,g,b))
    h,l,s = colorsys.rgb_to_hls(r,g,b)
    l = l + (1-l)*0.5
    rgb_new = colorsys.hls_to_rgb(h,l,s)
    return rgb_new
print(highlight_color((127,204,233)))

(0.4980392156862745, 0.8, 0.9137254901960784)
(0.7490196078431373, 0.8999999999999999, 0.9568627450980391)


In [53]:
from IPython.display import IFrame

url = 'https://neuroglancer-demo.appspot.com/#!%7B%22dimensions%22:%7B%22x%22:%5B1e-9%2C%22m%22%5D%2C%22y%22:%5B1e-9%2C%22m%22%5D%2C%22z%22:%5B1e-9%2C%22m%22%5D%7D%2C%22position%22:%5B28036.478515625%2C3525.743896484375%2C17757.845703125%5D%2C%22crossSectionOrientation%22:%5B1%2C0%2C0%2C0%5D%2C%22crossSectionScale%22:50%2C%22projectionOrientation%22:%5B0.8361419439315796%2C-0.22252444922924042%2C-0.4395635426044464%2C0.2411087155342102%5D%2C%22projectionScale%22:7482.7443018685735%2C%22layers%22:%5B%7B%22type%22:%22segmentation%22%2C%22source%22:%5B%22n5://s3://janelia-cosem-datasets/jrc_macrophage-2/jrc_macrophage-2.n5/labels/mito_seg%22%2C%22precomputed://s3://janelia-cosem-datasets/jrc_macrophage-2/neuroglancer/mesh/mito_seg%22%5D%2C%22tab%22:%22annotations%22%2C%22segments%22:%5B%221%22%2C%2210%22%2C%22100%22%2C%22101%22%2C%22102%22%2C%22103%22%2C%22104%22%2C%22105%22%2C%22106%22%2C%22107%22%2C%22108%22%2C%22109%22%2C%2211%22%2C%22110%22%2C%22111%22%2C%22112%22%2C%22113%22%2C%22114%22%2C%22115%22%2C%22116%22%2C%22117%22%2C%22118%22%2C%22119%22%2C%2212%22%2C%22120%22%2C%22121%22%2C%22122%22%2C%22123%22%2C%22124%22%2C%22125%22%2C%22126%22%2C%22127%22%2C%22128%22%2C%22129%22%2C%2213%22%2C%22130%22%2C%22131%22%2C%22132%22%2C%22133%22%2C%22134%22%2C%22135%22%2C%22136%22%2C%22137%22%2C%22138%22%2C%22139%22%2C%2214%22%2C%22140%22%2C%22141%22%2C%22142%22%2C%22143%22%2C%22144%22%2C%22145%22%2C%22146%22%2C%22147%22%2C%22148%22%2C%22149%22%2C%2215%22%2C%22150%22%2C%22151%22%2C%22152%22%2C%22153%22%2C%22154%22%2C%22155%22%2C%22156%22%2C%22157%22%2C%22158%22%2C%22159%22%2C%2216%22%2C%22160%22%2C%22161%22%2C%22162%22%2C%22163%22%2C%22164%22%2C%22165%22%2C%22166%22%2C%22167%22%2C%22168%22%2C%22169%22%2C%2217%22%2C%22170%22%2C%22171%22%2C%22172%22%2C%22173%22%2C%22174%22%2C%22175%22%2C%22176%22%2C%22177%22%2C%22178%22%2C%22179%22%2C%2218%22%2C%22180%22%2C%22181%22%2C%22182%22%2C%22183%22%2C%22184%22%2C%22185%22%2C%22186%22%2C%22187%22%2C%22188%22%2C%22189%22%2C%2219%22%2C%22190%22%2C%22191%22%2C%22192%22%2C%22193%22%2C%22194%22%2C%22195%22%2C%22196%22%2C%22197%22%2C%22198%22%2C%22199%22%2C%222%22%2C%2220%22%2C%22200%22%2C%22201%22%2C%22202%22%2C%22203%22%2C%22204%22%2C%22205%22%2C%22206%22%2C%22207%22%2C%22208%22%2C%22209%22%2C%2221%22%2C%22210%22%2C%22211%22%2C%22212%22%2C%22213%22%2C%22214%22%2C%22215%22%2C%22216%22%2C%22217%22%2C%22218%22%2C%22219%22%2C%2222%22%2C%22220%22%2C%22221%22%2C%22222%22%2C%22223%22%2C%22224%22%2C%22225%22%2C%22226%22%2C%22227%22%2C%22228%22%2C%22229%22%2C%2223%22%2C%22230%22%2C%22231%22%2C%22232%22%2C%22233%22%2C%22234%22%2C%22235%22%2C%22236%22%2C%22237%22%2C%22238%22%2C%22239%22%2C%2224%22%2C%22240%22%2C%22241%22%2C%22242%22%2C%22243%22%2C%22244%22%2C%22245%22%2C%22246%22%2C%22247%22%2C%22248%22%2C%22249%22%2C%2225%22%2C%22250%22%2C%22251%22%2C%22252%22%2C%22253%22%2C%22254%22%2C%22255%22%2C%22256%22%2C%22257%22%2C%22258%22%2C%22259%22%2C%2226%22%2C%22260%22%2C%22261%22%2C%22262%22%2C%22263%22%2C%22264%22%2C%22265%22%2C%22266%22%2C%22267%22%2C%22268%22%2C%22269%22%2C%2227%22%2C%22270%22%2C%22271%22%2C%22272%22%2C%22273%22%2C%22274%22%2C%22275%22%2C%22276%22%2C%22277%22%2C%22278%22%2C%22279%22%2C%2228%22%2C%22280%22%2C%22281%22%2C%22282%22%2C%22283%22%2C%22284%22%2C%22285%22%2C%22286%22%2C%22287%22%2C%22288%22%2C%22289%22%2C%2229%22%2C%22290%22%2C%22291%22%2C%22292%22%2C%22293%22%2C%22294%22%2C%22295%22%2C%22296%22%2C%22297%22%2C%22298%22%2C%22299%22%2C%223%22%2C%2230%22%2C%22300%22%2C%22301%22%2C%22302%22%2C%22303%22%2C%22304%22%2C%22305%22%2C%22306%22%2C%22307%22%2C%22308%22%2C%22309%22%2C%2231%22%2C%22310%22%2C%22311%22%2C%22312%22%2C%22313%22%2C%22314%22%2C%22315%22%2C%22316%22%2C%22317%22%2C%22318%22%2C%22319%22%2C%2232%22%2C%22320%22%2C%22321%22%2C%22322%22%2C%22323%22%2C%22324%22%2C%22325%22%2C%22326%22%2C%22327%22%2C%22328%22%2C%22329%22%2C%2233%22%2C%22330%22%2C%22331%22%2C%22332%22%2C%22333%22%2C%22334%22%2C%22335%22%2C%22336%22%2C%22337%22%2C%22338%22%2C%22339%22%2C%2234%22%2C%22340%22%2C%22341%22%2C%22342%22%2C%22343%22%2C%22344%22%2C%22345%22%2C%22346%22%2C%22347%22%2C%22348%22%2C%22349%22%2C%2235%22%2C%22350%22%2C%22351%22%2C%22352%22%2C%22353%22%2C%22354%22%2C%22355%22%2C%22356%22%2C%22357%22%2C%22358%22%2C%22359%22%2C%2236%22%2C%22360%22%2C%22361%22%2C%22362%22%2C%22363%22%2C%22364%22%2C%22365%22%2C%22366%22%2C%22367%22%2C%22368%22%2C%22369%22%2C%2237%22%2C%22370%22%2C%22371%22%2C%22372%22%2C%22373%22%2C%22374%22%2C%22375%22%2C%22376%22%2C%22377%22%2C%22378%22%2C%22379%22%2C%2238%22%2C%22380%22%2C%22381%22%2C%22382%22%2C%22383%22%2C%22384%22%2C%22385%22%2C%22386%22%2C%22387%22%2C%22388%22%2C%22389%22%2C%2239%22%2C%22390%22%2C%22391%22%2C%22392%22%2C%22393%22%2C%22394%22%2C%22395%22%2C%22396%22%2C%22397%22%2C%22398%22%2C%22399%22%2C%224%22%2C%2240%22%2C%22400%22%2C%22401%22%2C%22402%22%2C%22403%22%2C%22404%22%2C%22405%22%2C%22406%22%2C%22407%22%2C%22408%22%2C%22409%22%2C%2241%22%2C%22410%22%2C%22411%22%2C%22412%22%2C%22413%22%2C%22414%22%2C%22415%22%2C%22416%22%2C%22417%22%2C%22418%22%2C%22419%22%2C%2242%22%2C%22420%22%2C%22421%22%2C%22422%22%2C%22423%22%2C%22424%22%2C%22425%22%2C%22426%22%2C%22427%22%2C%22428%22%2C%22429%22%2C%2243%22%2C%22430%22%2C%22431%22%2C%22432%22%2C%22433%22%2C%22434%22%2C%22435%22%2C%22436%22%2C%22437%22%2C%22438%22%2C%22439%22%2C%2244%22%2C%22440%22%2C%22441%22%2C%22442%22%2C%22443%22%2C%22444%22%2C%22445%22%2C%22446%22%2C%22447%22%2C%22448%22%2C%22449%22%2C%2245%22%2C%22450%22%2C%22451%22%2C%22452%22%2C%22453%22%2C%22454%22%2C%22455%22%2C%22456%22%2C%22457%22%2C%22458%22%2C%22459%22%2C%2246%22%2C%22460%22%2C%22461%22%2C%22462%22%2C%22463%22%2C%22464%22%2C%22465%22%2C%22466%22%2C%22467%22%2C%22468%22%2C%22469%22%2C%2247%22%2C%22470%22%2C%22471%22%2C%22472%22%2C%22473%22%2C%22474%22%2C%22475%22%2C%22476%22%2C%22477%22%2C%22478%22%2C%22479%22%2C%2248%22%2C%22480%22%2C%22481%22%2C%22482%22%2C%22483%22%2C%22484%22%2C%22485%22%2C%22486%22%2C%22487%22%2C%22488%22%2C%22489%22%2C%2249%22%2C%22490%22%2C%22491%22%2C%22492%22%2C%22493%22%2C%22494%22%2C%22495%22%2C%22496%22%2C%22497%22%2C%22498%22%2C%22499%22%2C%225%22%2C%2250%22%2C%22500%22%2C%22501%22%2C%22502%22%2C%22503%22%2C%22504%22%2C%22505%22%2C%22506%22%2C%22507%22%2C%22508%22%2C%22509%22%2C%2251%22%2C%22510%22%2C%22511%22%2C%22512%22%2C%22513%22%2C%22514%22%2C%22515%22%2C%22516%22%2C%22517%22%2C%22518%22%2C%22519%22%2C%2252%22%2C%22520%22%2C%22521%22%2C%22522%22%2C%22523%22%2C%22524%22%2C%22525%22%2C%22526%22%2C%22527%22%2C%22528%22%2C%22529%22%2C%2253%22%2C%22530%22%2C%22531%22%2C%22532%22%2C%22533%22%2C%22534%22%2C%22535%22%2C%22536%22%2C%22537%22%2C%22538%22%2C%22539%22%2C%2254%22%2C%22540%22%2C%22541%22%2C%22542%22%2C%22543%22%2C%22544%22%2C%22545%22%2C%22546%22%2C%22547%22%2C%22548%22%2C%22549%22%2C%2255%22%2C%22550%22%2C%22551%22%2C%22552%22%2C%22553%22%2C%22554%22%2C%22555%22%2C%22556%22%2C%22557%22%2C%22558%22%2C%22559%22%2C%2256%22%2C%22560%22%2C%22561%22%2C%22562%22%2C%22563%22%2C%22564%22%2C%22565%22%2C%22566%22%2C%22567%22%2C%22568%22%2C%22569%22%2C%2257%22%2C%22570%22%2C%22571%22%2C%22572%22%2C%22573%22%2C%22574%22%2C%22575%22%2C%22576%22%2C%22577%22%2C%22578%22%2C%22579%22%2C%2258%22%2C%22580%22%2C%22581%22%2C%22582%22%2C%22583%22%2C%22584%22%2C%22585%22%2C%22586%22%2C%22587%22%2C%22588%22%2C%22589%22%2C%2259%22%2C%22590%22%2C%22591%22%2C%22592%22%2C%22593%22%2C%22594%22%2C%22595%22%2C%22596%22%2C%22597%22%2C%22598%22%2C%22599%22%2C%226%22%2C%2260%22%2C%22600%22%2C%22601%22%2C%22602%22%2C%22603%22%2C%22604%22%2C%22605%22%2C%22606%22%2C%22607%22%2C%22608%22%2C%22609%22%2C%2261%22%2C%22610%22%2C%22611%22%2C%22612%22%2C%22613%22%2C%22614%22%2C%22615%22%2C%22616%22%2C%22617%22%2C%22618%22%2C%22619%22%2C%2262%22%2C%22620%22%2C%22621%22%2C%22622%22%2C%22623%22%2C%22624%22%2C%22625%22%2C%22626%22%2C%22627%22%2C%22628%22%2C%22629%22%2C%2263%22%2C%2264%22%2C%2265%22%2C%2266%22%2C%2267%22%2C%2268%22%2C%2269%22%2C%227%22%2C%2270%22%2C%2271%22%2C%2272%22%2C%2273%22%2C%2274%22%2C%2275%22%2C%2276%22%2C%2277%22%2C%2278%22%2C%2279%22%2C%228%22%2C%2280%22%2C%2281%22%2C%2282%22%2C%2283%22%2C%2284%22%2C%2285%22%2C%2286%22%2C%2287%22%2C%2288%22%2C%2289%22%2C%229%22%2C%2290%22%2C%2291%22%2C%2292%22%2C%2293%22%2C%2294%22%2C%2295%22%2C%2296%22%2C%2297%22%2C%2298%22%2C%2299%22%5D%2C%22segmentDefaultColor%22:%22#008000%22%2C%22name%22:%22mito_seg%22%7D%2C%7B%22type%22:%22image%22%2C%22source%22:%7B%22url%22:%22precomputed://s3://janelia-cosem-datasets/jrc_macrophage-2/neuroglancer/em/fibsem-uint8.precomputed%22%2C%22transform%22:%7B%22matrix%22:%5B%5B1%2C0%2C0%2C0%5D%2C%5B0%2C-1%2C0%2C8000%5D%2C%5B0%2C0%2C1%2C0%5D%5D%2C%22outputDimensions%22:%7B%22x%22:%5B1e-9%2C%22m%22%5D%2C%22y%22:%5B1e-9%2C%22m%22%5D%2C%22z%22:%5B1e-9%2C%22m%22%5D%7D%7D%7D%2C%22tab%22:%22rendering%22%2C%22opacity%22:0.75%2C%22blend%22:%22additive%22%2C%22shader%22:%22#uicontrol%20invlerp%20normalized%28range=%5B214%2C%20233%5D%2C%20window=%5B0%2C%20255%5D%29%5Cn%20%20%20%20%20%20%20%20#uicontrol%20int%20invertColormap%20slider%28min=0%2C%20max=1%2C%20step=1%2C%20default=0%29%5Cn%20%20%20%20%20%20%20%20#uicontrol%20vec3%20color%20color%28default=%5C%22white%5C%22%29%5Cn%20%20%20%20%20%20%20%20float%20inverter%28float%20val%2C%20int%20invert%29%20%7Breturn%200.5%20+%20%28%282.0%20%2A%20%28-float%28invert%29%20+%200.5%29%29%20%2A%20%28val%20-%200.5%29%29%3B%7D%5Cn%20%20%20%20%20%20%20%20%20%20void%20main%28%29%20%7B%5Cn%20%20%20%20%20%20%20%20%20%20emitRGB%28color%20%2A%20inverter%28normalized%28%29%2C%20invertColormap%29%29%3B%5Cn%20%20%20%20%20%20%20%20%7D%22%2C%22name%22:%22fibsem-uint8%22%7D%5D%2C%22selectedLayer%22:%7B%22visible%22:true%2C%22layer%22:%22mito_seg%22%7D%2C%22crossSectionBackgroundColor%22:%22#000000%22%2C%22layout%22:%223d%22%7D'
i=IFrame(url, width=800, height=400)
print(i._repr_html_())



        <iframe
            width="800"
            height="400"
            src="https://neuroglancer-demo.appspot.com/#!%7B%22dimensions%22:%7B%22x%22:%5B1e-9%2C%22m%22%5D%2C%22y%22:%5B1e-9%2C%22m%22%5D%2C%22z%22:%5B1e-9%2C%22m%22%5D%7D%2C%22position%22:%5B28036.478515625%2C3525.743896484375%2C17757.845703125%5D%2C%22crossSectionOrientation%22:%5B1%2C0%2C0%2C0%5D%2C%22crossSectionScale%22:50%2C%22projectionOrientation%22:%5B0.8361419439315796%2C-0.22252444922924042%2C-0.4395635426044464%2C0.2411087155342102%5D%2C%22projectionScale%22:7482.7443018685735%2C%22layers%22:%5B%7B%22type%22:%22segmentation%22%2C%22source%22:%5B%22n5://s3://janelia-cosem-datasets/jrc_macrophage-2/jrc_macrophage-2.n5/labels/mito_seg%22%2C%22precomputed://s3://janelia-cosem-datasets/jrc_macrophage-2/neuroglancer/mesh/mito_seg%22%5D%2C%22tab%22:%22annotations%22%2C%22segments%22:%5B%221%22%2C%2210%22%2C%22100%22%2C%22101%22%2C%22102%22%2C%22103%22%2C%22104%22%2C%22105%22%2C%22106%22%2C%22107%22%2C%22108%22%2C%

In [44]:
from IPython.display import IFrame

url = 'https://wikipedia.org'
i = IFrame(url, width=800, height=400)
display(i.iframe)


'\n        <iframe\n            width="{width}"\n            height="{height}"\n            src="{src}{params}"\n            frameborder="0"\n            allowfullscreen\n            {extras}\n        ></iframe>\n        '